# Autour du paradoxe de Simpson

Ce document présente une analyse de données pour le MOOC recherche reproductible. Le but est d'analyser les données autour du paradoxe de Simpson, qui donne l'impression - en premier lieu - donner des conclusions surprenantes sur l'effet du tabagisme sur la santé.

## Importing and checking the data

In [1]:
%matplotlib inline
import matplotlib.pyplot as plt
import pandas as pd

Nous récupérons les données sous format CSV depuis le Gitlab du MOOC.

In [2]:
data_url ="https://gitlab.inria.fr/learninglab/mooc-rr/mooc-rr-ressources/-/raw/master/module3/Practical_session/Subject6_smoking.csv?inline=false"

In [3]:
raw_data = pd.read_csv(data_url)

Regardons visuellement le dataset.

In [4]:
raw_data

Smoker Status   Age
0       Yes  Alive  21.0
1       Yes  Alive  19.3
2        No   Dead  57.5
3        No  Alive  47.1
4       Yes  Alive  81.4
5        No  Alive  36.8
6        No  Alive  23.8
7       Yes   Dead  57.5
8       Yes  Alive  24.8
9       Yes  Alive  49.5
10      Yes  Alive  30.0
11       No   Dead  66.0
12      Yes  Alive  49.2
13       No  Alive  58.4
14       No   Dead  60.6
15       No  Alive  25.1
16       No  Alive  43.5
17       No  Alive  27.1
18       No  Alive  58.3
19      Yes  Alive  65.7
20       No   Dead  73.2
21      Yes  Alive  38.3
22       No  Alive  33.4
23      Yes   Dead  62.3
24       No  Alive  18.0
25       No  Alive  56.2
26      Yes  Alive  59.2
27       No  Alive  25.8
28       No   Dead  36.9
29       No  Alive  20.2
...     ...    ...   ...
1284    Yes   Dead  36.0
1285    Yes  Alive  48.3
1286     No  Alive  63.1
1287     No  Alive  60.8
1288    Yes   Dead  39.3
1289     No  Alive  36.7
1290     No  Alive  63.8
1291     No   Dead  71.3
1292     No  Alive  57.7
1293     No  Alive  63.2
1294     No  Alive  46.6
1295    Yes   Dead  82.4
1296    Yes  Alive  38.3
1297    Yes  Alive  32.7
1298     No  Alive  39.7
1299    Yes   Dead  60.0
1300     No   Dead  71.0
1301     No  Alive  20.5
1302     No  Alive  44.4
1303    Yes  Alive  31.2
1304    Yes  Alive  47.8
1305    Yes  Alive  60.9
1306     No   Dead  61.4
1307    Yes  Alive  43.0
1308     No  Alive  42.1
1309    Yes  Alive  35.9
1310     No  Alive  22.3
1311    Yes   Dead  62.1
1312     No   Dead  88.6
1313     No  Alive  39.1

[1314 rows x 3 columns]

Nous allons maintenant vérifier si aucune donnée n'est manquante, et si les différentes lignes concordent entre elles.

In [5]:
raw_data[raw_data.isnull().any(axis=1)]

Empty DataFrame
Columns: [Smoker, Status, Age]
Index: []

In [6]:
raw_data[(raw_data['Smoker'] != "Yes") & (raw_data['Smoker'] != "No")]

Empty DataFrame
Columns: [Smoker, Status, Age]
Index: []

In [7]:
raw_data[(raw_data['Status'] != "Alive") & (raw_data['Status'] != "Dead")]

Empty DataFrame
Columns: [Smoker, Status, Age]
Index: []

Le dataset paraît correct, et les données brutes sont ainsi utilisées pour l'analyse.

In [8]:
data = raw_data.copy()

## Taux de mortalité (question 1)

Nous allons calculer le taux de mortalité sur la période pour les deux groupes de femmes: fumeuses et non fumeuses, et représenter les résultats sous forme d'un tableau.

In [9]:
alive = [len(data[(data['Smoker'] == "Yes") & (data['Status'] == "Alive")].index), len(data[(data['Smoker'] == "No") & (data['Status'] == "Alive")].index)]
dead = [len(data[(data['Smoker'] == "Yes") & (data['Status'] == "Dead")].index), len(data[(data['Smoker'] == "No") & (data['Status'] == "Dead")].index)]
deathrate = [dead[0]/(alive[0] + dead[0]), dead[1]/(alive[1] + dead[1])]

print(pd.DataFrame([alive, dead, deathrate], ["Vivantes", "Mortes", "Taux mortalité"], ["Smokers", "Non-Smokers"]))

                   Smokers  Non-Smokers
Vivantes        443.000000   502.000000
Mortes          139.000000   230.000000
Taux mortalité    0.238832     0.314208


On remarque que le taux de mortalité est - nettement - plus élevé dans le groupe des non fumeuses, ce qui constitue le paradoxe de Simpson, vu que le sens commun ferait s'attendre à la conclusion inverse.

## Taux de mortalité par classes d'age (question 2)

Nous allons regarder si les résultats persistent en prenant en compte les différentes classes d'age

In [10]:
classes_breaks = [0,35,55,65,150] 
tab_alive = [ [len(data[(data['Smoker'] == "Yes") & (data['Status'] == "Alive") & (classes_breaks[i] <= data['Age']) & (data['Age'] < classes_breaks[i+1])]), len(data[(data['Smoker'] == "No") & (data['Status'] == "Alive") & (classes_breaks[i] <= data['Age']) & (data['Age'] < classes_breaks[i+1])])] for i in [0,1,2,3]]
tab_dead = [ [len(data[(data['Smoker'] == "Yes") & (data['Status'] == "Dead") & (classes_breaks[i] <= data['Age']) & (data['Age'] < classes_breaks[i+1])]), len(data[(data['Smoker'] == "No") & (data['Status'] == "Dead") & (classes_breaks[i] <= data['Age']) & (data['Age'] < classes_breaks[i+1])])] for i in [0,1,2,3]]
tab_deathrate = [ [tab_dead[i][0]/(tab_dead[i][0]+tab_alive[i][0]) , tab_dead[i][1]/(tab_dead[i][1]+tab_alive[i][1])] for i in [0,1,2,3]]

print(pd.DataFrame(tab_deathrate, ["18-34","35-54","55-64","65+"], ["Smokers", "Non-Smokers"]))

        Smokers  Non-Smokers
18-34  0.037037     0.026432
35-54  0.170306     0.099476
55-64  0.443478     0.330579
65+    0.857143     0.854922


On remarque cette fois que, pour chaque classe d'âge, le résultat est attendu où le taux de mortalité est nettement supérieur pour le groupe des fumeuses, sauf pour les plus de 65 ans où les résultats sont sensiblement égaux.

Une explication possible de ce paradoxe est que le groupe des non fumeuses contient plus de personnes agées (proportionnellement), vu que les non fumeuses vivent plus longtemps, et du coup il contient également un taux de mortalité plus élevé, vu que l'âge est la principale variable explicative du taux de décès.

## Vérification de l'hypothèse - régression logistique (question 3)

Pour commencer on va rajouter les variables de type boolean dans le dataset, pour représenter les variables Status et Smoker.

In [11]:
dead_bool = [(data['Status'][i] == "Dead") for i in range(len(data))]
data['Dead?'] = dead_bool
smoke_bool = [(data['Smoker'][i] == "Yes") for i in range(len(data))]
data['Smoke?'] = smoke_bool

 Nous allons tester les hypothèses par régression logistique.

In [12]:
import numpy as np
import statsmodels.api as sm


In [13]:
x1 = data['Age'].values.reshape(-1,1)
x2 = data['Smoke?'].values.reshape(-1,1)
x = np.hstack((x1,x2))
x = sm.add_constant(x)
y = data['Dead?']

In [14]:
model = sm.Logit(y, x)
result = model.fit(method='newton')

Optimization terminated successfully.
         Current function value: 0.381244
         Iterations 7


In [15]:
result.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                           Logit Regression Results                           
==============================================================================
Dep. Variable:                  Dead?   No. Observations:                 1314
Model:                          Logit   Df Residuals:                     1311
Method:                           MLE   Df Model:                            2
Date:                Tue, 01 Sep 2020   Pseudo R-squ.:                  0.3579
Time:                        10:16:00   Log-Likelihood:                -500.95
converged:                       True   LL-Null:                       -780.16
                                        LLR p-value:                5.534e-122
==============================================================================
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
const         -6.3519      0.360    -17.637      0.000      -7.058      -5.646
x1             0.0998      0.006     17.290      0.000       0.089       0.111
x2             0.2787      0.165      1.689      0.091      -0.045       0.602
==============================================================================
"""

Le tableau précédent donne les résultats de la régression logistique, avec x1 qui représente l'âge, et x2 qui représente le status (fumeuse ou non fumeuse). Le modèle cherche donc à expliquer la variable "Dead ?" à l'aide des variables âge et fumeur ou non. Les résultats montrent un p-value à 0.09 pour le status de fumeur, ce qui signifie que l'on peut rejeter l'hypothèse nulle pour une valeur significative de 10%, mais pas pour 5%. De plus le coefficient associé est positif, on peut donc en conclure que le fait de fumer impacte négativement l'espérance de vie, pour un seuil significatif de 10%. Des recherches plus approfondies seraient nécessaires pour établir des conclusions plus claires.